In [11]:
#!/usr/bin/env python3
"""
OCR for Large TIFF Images with Overlapping Crops

This script processes large TIFF images by:
1. Breaking them into overlapping chunks
2. Performing OCR on each chunk
3. Combining results while handling duplicate detections
4. Returning a dictionary with text and pixel locations
5. Visualizing detected text on the original image
"""

import os
import sys
import argparse
from pathlib import Path
import json
from PIL import Image, ImageDraw, ImageFont
import pytesseract
import numpy as np
from tqdm import tqdm
import cv2
import math

def install_requirements():
    """
    Check and install required packages if they're missing
    """
    try:
        import pip
        required_packages = ["pillow", "pytesseract", "numpy", "tqdm", "opencv-python"]
        for package in required_packages:
            try:
                __import__(package.replace("-", "_"))
                print(f"✓ {package} is already installed")
            except ImportError:
                print(f"Installing {package}...")
                pip.main(["install", package])
                print(f"✓ {package} installed successfully")
    except Exception as e:
        print(f"Error installing packages: {e}")
        sys.exit(1)

def verify_tesseract_installation():
    """
    Verify Tesseract OCR is installed and available
    """
    try:
        version = pytesseract.get_tesseract_version()
        print(f"✓ Tesseract is installed (version {version})")
        return True
    except pytesseract.TesseractNotFoundError:
        print("✗ Tesseract is not installed or not in PATH")
        print("\nTo install Tesseract on macOS:")
        print("1. Install Homebrew if not already installed:")
        print("   /bin/bash -c \"$(curl -fsSL https://raw.githubusercontent.com/Homebrew/install/HEAD/install.sh)\"")
        print("2. Install Tesseract:")
        print("   brew install tesseract")
        print("\nAfter installation, restart your terminal and run this script again.")
        return False

def crop_image_with_overlap(image_path, crop_size=(1000, 1000), overlap_percent=15):
    """
    Crop a large image into overlapping chunks
    
    Args:
        image_path: Path to the TIFF image
        crop_size: Size of each crop (width, height)
        overlap_percent: Percentage of overlap between adjacent crops
        
    Returns:
        List of tuples containing (cropped_image, x_offset, y_offset)
    """
    try:
        # Open the image
        image = Image.open(image_path)
        width, height = image.size
        
        # Calculate step sizes with overlap
        x_step = int(crop_size[0] * (1 - overlap_percent/100))
        y_step = int(crop_size[1] * (1 - overlap_percent/100))
        
        crops = []
        
        # Crop the image with overlap
        for y in range(0, height, y_step):
            for x in range(0, width, x_step):
                # Calculate the crop boundaries
                right = min(x + crop_size[0], width)
                bottom = min(y + crop_size[1], height)
                
                # Ensure we don't miss pixels at the edges
                if right == width and x > 0:
                    x = max(0, width - crop_size[0])
                if bottom == height and y > 0:
                    y = max(0, height - crop_size[1])
                
                # Extract the crop
                crop = image.crop((x, y, right, bottom))
                crops.append((crop, x, y))
                
        return crops, (width, height)  # Return crops and image dimensions
    except Exception as e:
        print(f"Error cropping image: {e}")
        return [], (0, 0)

def perform_ocr(image, config='', confidence_threshold=0, detect_orientation=True, multi_angle=False):
    """
    Perform OCR on an image and extract text with bounding boxes
    
    Args:
        image: PIL Image object
        config: Tesseract configuration string
        confidence_threshold: Minimum confidence score to keep (0-100)
        detect_orientation: Auto-detect text orientation
        multi_angle: Try multiple angle rotations for improved recognition
        
    Returns:
        List of dictionaries with text and bounding box information
    """
    # Convert PIL Image to OpenCV format
    img_cv = cv2.cvtColor(np.array(image), cv2.COLOR_RGB2BGR)
    
    results = []
    
    # Add orientation detection to config if requested
    orientation_config = config
    if detect_orientation:
        orientation_config += ' --psm 1'  # Automatic page segmentation with OSD
    
    # Try multiple orientations if requested
    angles = [0]  # Default is just the original orientation
    if multi_angle:
        angles = [0, 90, 180, 270]  # Try all major orientations
    
    for angle in angles:
        # Rotate image if needed
        if angle != 0:
            h, w = img_cv.shape[:2]
            center = (w // 2, h // 2)
            rotation_matrix = cv2.getRotationMatrix2D(center, angle, 1.0)
            rotated_img = cv2.warpAffine(img_cv, rotation_matrix, (w, h), flags=cv2.INTER_CUBIC, borderMode=cv2.BORDER_REPLICATE)
            current_img = rotated_img
        else:
            current_img = img_cv
        
        # Get OCR data including bounding boxes
        ocr_data = pytesseract.image_to_data(current_img, output_type=pytesseract.Output.DICT, config=orientation_config)
        
        num_boxes = len(ocr_data['text'])
        
        for i in range(num_boxes):
            # Filter by confidence threshold
            if int(ocr_data['conf'][i]) >= confidence_threshold and ocr_data['text'][i].strip():
                x = ocr_data['left'][i]
                y = ocr_data['top'][i]
                w = ocr_data['width'][i]
                h = ocr_data['height'][i]
                
                # If the image was rotated, transform the coordinates back
                if angle != 0:
                    # Get corner points of the text box
                    corners = np.array([
                        [x, y],
                        [x + w, y],
                        [x + w, y + h],
                        [x, y + h]
                    ], dtype=np.float32)
                    
                    # Rotate back to original orientation
                    center = np.array([img_cv.shape[1] // 2, img_cv.shape[0] // 2])
                    theta = -angle * np.pi / 180.0  # convert to radians and reverse the angle
                    
                    # Rotation matrix
                    R = np.array([
                        [np.cos(theta), -np.sin(theta)],
                        [np.sin(theta), np.cos(theta)]
                    ])
                    
                    # Rotate points
                    rotated_corners = []
                    for corner in corners:
                        # Translate point to origin, rotate, and translate back
                        corner = corner - center
                        corner = np.dot(R, corner)
                        corner = corner + center
                        rotated_corners.append(corner)
                    
                    # Calculate new bounding box
                    rotated_corners = np.array(rotated_corners)
                    min_x = np.min(rotated_corners[:, 0])
                    min_y = np.min(rotated_corners[:, 1])
                    max_x = np.max(rotated_corners[:, 0])
                    max_y = np.max(rotated_corners[:, 1])
                    
                    # Update coordinates
                    x, y = int(min_x), int(min_y)
                    w, h = int(max_x - min_x), int(max_y - min_y)
                    
                results.append({
                    'text': ocr_data['text'][i],
                    'bbox': (x, y, x + w, y + h),
                    'conf': ocr_data['conf'][i],
                    'angle': angle
                })
    
    return results

def remove_duplicates(all_results, iou_threshold=0.5):
    """
    Remove duplicate text detections based on IoU (Intersection over Union)
    
    Args:
        all_results: List of OCR results
        iou_threshold: Threshold for considering detections as duplicates
        
    Returns:
        List of unique OCR results
    """
    if not all_results:
        return []
    
    def calculate_iou(box1, box2):
        """Calculate Intersection over Union for two boxes"""
        x1_1, y1_1, x2_1, y2_1 = box1
        x1_2, y1_2, x2_2, y2_2 = box2
        
        # Calculate intersection area
        x_left = max(x1_1, x1_2)
        y_top = max(y1_1, y1_2)
        x_right = min(x2_1, x2_2)
        y_bottom = min(y2_1, y2_2)
        
        if x_right < x_left or y_bottom < y_top:
            return 0.0
        
        intersection_area = (x_right - x_left) * (y_bottom - y_top)
        
        # Calculate union area
        box1_area = (x2_1 - x1_1) * (y2_1 - y1_1)
        box2_area = (x2_2 - x1_2) * (y2_2 - y1_2)
        union_area = box1_area + box2_area - intersection_area
        
        if union_area == 0:
            return 0.0
            
        return intersection_area / union_area
    
    # Sort results by confidence (decreasing)
    sorted_results = sorted(all_results, key=lambda x: x['conf'], reverse=True)
    
    unique_results = []
    used_indices = set()
    
    for i, result in enumerate(sorted_results):
        if i in used_indices:
            continue
            
        unique_results.append(result)
        
        # Mark similar boxes as used
        for j in range(i + 1, len(sorted_results)):
            if j in used_indices:
                continue
                
            if sorted_results[i]['text'] == sorted_results[j]['text']:
                iou = calculate_iou(sorted_results[i]['bbox'], sorted_results[j]['bbox'])
                if iou > iou_threshold:
                    used_indices.add(j)
    
    return unique_results

def generate_visualization(image_path, ocr_results, output_path, show_confidence=True, max_size=None):
    """
    Generate a visualization of OCR results overlaid on the original image
    
    Args:
        image_path: Path to the original image
        ocr_results: Dictionary of OCR results
        output_path: Path to save the visualization image
        show_confidence: Whether to show confidence scores
        max_size: Max size for visualization (width, height) to handle large images
    """
    try:
        # Open the original image
        original_image = Image.open(image_path)
        width, height = original_image.size
        
        # Always maintain the original aspect ratio
        viz_image = original_image.copy()
        resize_factor = 1.0
        
        # Resize only if needed, while maintaining the exact aspect ratio
        if max_size and (width > max_size[0] or height > max_size[1]):
            # Calculate resize ratio while preserving aspect ratio
            ratio = min(max_size[0] / width, max_size[1] / height)
            new_size = (int(width * ratio), int(height * ratio))
            
            # Resize the image with the exact ratio
            viz_image = original_image.resize(new_size, Image.Resampling.LANCZOS)
            resize_factor = ratio
            print(f"Resized visualization from {width}x{height} to {new_size[0]}x{new_size[1]} (ratio: {ratio:.3f})")
        else:
            viz_image = original_image.copy()
            resize_factor = 1.0
        
        # Create a drawing object
        draw = ImageDraw.Draw(viz_image)
        
        # Try to load a font, use default if not available
        try:
            # Try to load a font that supports a wide range of characters
            font_size = 12
            font = ImageFont.truetype("Arial", font_size)
        except IOError:
            # Use default font if Arial is not available
            font = ImageFont.load_default()
        
        # Define colors for different angles for better visualization
        angle_colors = {
            0: "red",      # Horizontal text (0 degrees)
            90: "green",   # Vertical text (90 degrees)
            180: "blue",   # Upside-down text (180 degrees)
            270: "purple"  # Vertical text (270 degrees)
        }
        
        # Draw rectangles and text for each detection
        for key, item in ocr_results.items():
            # Scale the coordinates based on resize factor
            x1 = int(item['location']['x1'] * resize_factor)
            y1 = int(item['location']['y1'] * resize_factor)
            x2 = int(item['location']['x2'] * resize_factor)
            y2 = int(item['location']['y2'] * resize_factor)
            
            # Get the angle if available, default to 0
            angle = item.get('angle', 0)
            outline_color = angle_colors.get(angle, "red")
            
            # Draw rectangle
            draw.rectangle([(x1, y1), (x2, y2)], outline=outline_color, width=2)
            
            # Draw diagonal lines for the rectangle to better visualize orientation
            draw.line([(x1, y1), (x2, y2)], fill=outline_color, width=1)
            draw.line([(x1, y2), (x2, y1)], fill=outline_color, width=1)
            
            # Prepare text for display
            display_text = item['text']
            if show_confidence:
                display_text += f" ({item['confidence']:.1f}%)"
            if 'angle' in item:
                display_text += f" [{item['angle']}°]"
            
            # Draw text background
            text_width = len(display_text) * (font_size / 2)
            text_bg_coords = [x1, y1 - font_size - 4, int(x1 + text_width), y1]
            draw.rectangle(text_bg_coords, fill=outline_color)
            
            # Draw text
            draw.text((x1, y1 - font_size - 2), display_text, fill="white", font=font)
        
        # Save the visualization
        viz_image.save(output_path)
        print(f"Visualization saved to {output_path}")
        
        return True
    except Exception as e:
        print(f"Error generating visualization: {e}")
        return False

def process_large_tiff(image_path, crop_size=(1000, 1000), overlap_percent=15, 
                      tesseract_config='', lang='eng', confidence_threshold=0,
                      detect_orientation=True, multi_angle=False):
    """
    Process a large TIFF image for OCR with overlapping crops
    
    Args:
        image_path: Path to the TIFF image
        crop_size: Size of crops (width, height)
        overlap_percent: Percentage of overlap between crops
        tesseract_config: Additional Tesseract configuration
        lang: Language for OCR
        confidence_threshold: Minimum confidence score (0-100)
        detect_orientation: Automatically detect text orientation
        multi_angle: Process image at multiple angles for non-horizontal text
        
    Returns:
        Dictionary with text entries and their locations, and original image dimensions
    """
    config = f'-l {lang} {tesseract_config}'
    
    # Step 1: Crop the image with overlap
    print(f"Cropping image with {overlap_percent}% overlap...")
    crops, original_size = crop_image_with_overlap(image_path, crop_size, overlap_percent)
    print(f"Created {len(crops)} overlapping crops")
    
    # Step 2: Perform OCR on each crop
    all_results = []
    print(f"Performing OCR on crops with confidence threshold: {confidence_threshold}...")
    if detect_orientation:
        print("Text orientation detection enabled")
    if multi_angle:
        print("Multi-angle text detection enabled (0°, 90°, 180°, 270°)")
    
    for i, (crop, x_offset, y_offset) in enumerate(tqdm(crops)):
        # Get OCR results for this crop
        crop_results = perform_ocr(crop, config, confidence_threshold, detect_orientation, multi_angle)
        
        # Adjust bounding box coordinates to original image space
        for result in crop_results:
            x1, y1, x2, y2 = result['bbox']
            result['bbox'] = (x1 + x_offset, y1 + y_offset, x2 + x_offset, y2 + y_offset)
            result['crop_index'] = i
        
        all_results.extend(crop_results)
    
    # Step 3: Remove duplicates
    print("Removing duplicate detections...")
    unique_results = remove_duplicates(all_results)
    print(f"Found {len(unique_results)} unique text elements")
    
    # Step 4: Format results as a dictionary
    result_dict = {}
    for i, item in enumerate(unique_results):
        key = f"text_{i+1}"
        result_dict[key] = {
            'text': item['text'],
            'location': {
                'x1': item['bbox'][0],
                'y1': item['bbox'][1],
                'x2': item['bbox'][2],
                'y2': item['bbox'][3]
            },
            'confidence': float(item['conf'])
        }
        
        # Add orientation information if available
        if 'angle' in item:
            result_dict[key]['angle'] = item['angle']
    
    return result_dict, original_size

def main(input_dir_path, output_dir_path):
    parser = argparse.ArgumentParser(
        description='Batch OCR for large TIFF images with overlapping crops'
    )
   # parser.add_argument(
      #  '--input_dir', '-i', required=True,
       # help='存放待 OCR 的 TIFF 图像的文件夹路径'
   # )
    #parser.add_argument(
       # '--output_dir', '-O', required=True,
       # help='OCR 结果 JSON 输出文件夹路径'
    #)
    parser.add_argument('--crop-width', type=int, default=500,
                        help='每个 crop 的宽度 (默认 500)')
    parser.add_argument('--crop-height', type=int, default=500,
                        help='每个 crop 的高度 (默认 500)')
    parser.add_argument('--overlap', type=float, default=50,
                        help='crop 重叠比例，百分比 (默认 50)')
    parser.add_argument('--lang', default='eng',
                        help='OCR 语言 (默认 eng)')
    parser.add_argument('--dpi', type=int, default=300,
                        help='OCR DPI 设置 (默认 300)')
    parser.add_argument('--install', action='store_true',
                        help='安装依赖包后再退出')
    parser.add_argument('--confidence', type=float, default=0,
                        help='置信度阈值 (0-100)')
    parser.add_argument('--detect-orientation', action='store_true',
                        help='自动检测文字方向')
    parser.add_argument('--multi-angle', action='store_true',
                        help='对多角度(0°,90°,180°,270°)做 OCR')
    parser.add_argument('--oem', type=int, choices=[0,1,2,3], default=3,
                        help='Tesseract 引擎模式 (0–3)')
    parser.add_argument('--psm', type=int, choices=range(0,14), default=3,
                        help='Tesseract 分页模式 (0–13)')
    args = parser.parse_args()

    if args.install:
        install_requirements()
        return

    if not verify_tesseract_installation():
        return

    # 构造 Tesseract config
    config = f'--oem {args.oem} --psm {args.psm}'
    if args.dpi:
        config += f' --dpi {args.dpi}'

    #input_dir = Path(args.input_dir)
   # output_dir = Path(args.output_dir)
    input_dir = r"D:\testing_data_SScale_tif"
    output_dir = r"D:\ocr_output"
    output_dir.mkdir(parents=True, exist_ok=True)

    # 收集所有 .tif/.tiff 文件
    image_paths = list(input_dir.glob("*.tif")) + list(input_dir.glob("*.tiff"))
    if not image_paths:
        print(f"未在 {input_dir} 下找到任何 .tif/.tiff 文件")
        return

    for image_path in tqdm(image_paths, desc="Batch OCR"):
        print(f"\nProcessing {image_path.name} ...")
        try:
            results, _ = process_large_tiff(
                image_path,
                crop_size=(args.crop_width, args.crop_height),
                overlap_percent=args.overlap,
                tesseract_config=config,
                lang=args.lang,
                confidence_threshold=args.confidence,
                detect_orientation=args.detect_orientation,
                multi_angle=args.multi_angle
            )
            out_file = output_dir / f"{image_path.stem}.json"
            with open(out_file, 'w', encoding='utf-8') as f:
                json.dump(results, f, indent=2, ensure_ascii=False)
            print(f"✔ Saved JSON to {out_file}")
        except Exception as e:
            print(f"✗ Failed on {image_path.name}: {e}")

    print("\nBatch OCR 完成。")

In [17]:
def main(input_dir_path, output_dir_path,
         crop_width=500, crop_height=500, overlap=50, lang='eng', dpi=300,
         confidence=0, detect_orientation=False, multi_angle=False,
         oem=3, psm=3, install=False): # Added parameters for direct passing
    # Re-initialize parser for internal calls, or remove required=True from add_argument calls
    # for a more flexible main, and let the calling code handle requiredness.
    # For this example, we'll simulate the args being parsed.
    parser = argparse.ArgumentParser(
        description='Batch OCR for large TIFF images with overlapping crops'
    )
    parser.add_argument('--input_dir', '-i', required=True, help='存放待 OCR 的 TIFF 图像的文件夹路径')
    parser.add_argument('--output_dir', '-O', required=True, help='OCR 结果 JSON 输出文件夹路径')
    parser.add_argument('--crop-width', type=int, default=500, help='每个 crop 的宽度 (默认 500)')
    parser.add_argument('--crop-height', type=int, default=500, help='每个 crop 的高度 (默认 500)')
    parser.add_argument('--overlap', type=float, default=50, help='crop 重叠比例，百分比 (默认 50)')
    parser.add_argument('--lang', default='eng', help='OCR 语言 (默认 eng)')
    parser.add_argument('--dpi', type=int, default=300, help='OCR DPI 设置 (默认 300)')
    parser.add_argument('--install', action='store_true', help='安装依赖包后再退出')
    parser.add_argument('--confidence', type=float, default=0, help='置信度阈值 (0-100)')
    parser.add_argument('--detect-orientation', action='store_true', help='自动检测文字方向')
    parser.add_argument('--multi-angle', action='store_true', help='对多角度(0°,90°,180°,270°)做 OCR')
    parser.add_argument('--oem', type=int, choices=[0,1,2,3], default=3, help='Tesseract 引擎模式 (0–3)')
    parser.add_argument('--psm', type=int, choices=range(0,14), default=3, help='Tesseract 分页模式 (0–13)')

    # Simulate command-line arguments by passing a list
    # This is where you would set your paths directly in the code
    args = parser.parse_args([
        '--input_dir', input_dir_path,
        '--output_dir', output_dir_path,
        '--crop-width', str(crop_width), # Ensure non-string values are converted
        '--crop-height', str(crop_height),
        '--overlap', str(overlap),
        '--lang', lang,
        '--dpi', str(dpi),
        '--confidence', str(confidence),
        # Add other arguments if needed, for store_true actions, just omit them if False
        # If install is True: '--install'
        # If detect_orientation is True: '--detect-orientation'
        # If multi_angle is True: '--multi-angle'
        '--oem', str(oem),
        '--psm', str(psm)
    ])

    if args.install:
        install_requirements()
        return

    if not verify_tesseract_installation():
        return

    # 构造 Tesseract config
    config = f'--oem {args.oem} --psm {args.psm}'
    if args.dpi:
        config += f' --dpi {args.dpi}'

    input_dir = Path(args.input_dir)
    output_dir = Path(args.output_dir)
    output_dir.mkdir(parents=True, exist_ok=True)

    # 收集所有 .tif/.tiff 文件
    image_paths = list(input_dir.glob("*.tif")) + list(input_dir.glob("*.tiff"))
    if not image_paths:
        print(f"未在 {input_dir} 下找到任何 .tif/.tiff 文件")
        return

    for image_path in tqdm(image_paths, desc="Batch OCR"):
        print(f"\nProcessing {image_path.name} ...")
        try:
            results, _ = process_large_tiff(
                image_path,
                crop_size=(args.crop_width, args.crop_height),
                overlap_percent=args.overlap,
                tesseract_config=config,
                lang=args.lang,
                confidence_threshold=args.confidence,
                detect_orientation=args.detect_orientation,
                multi_angle=args.multi_angle
            )
            out_file = output_dir / f"{image_path.stem}.json"
            with open(out_file, 'w', encoding='utf-8') as f:
                json.dump(results, f, indent=2, ensure_ascii=False)
            print(f"✔ Saved JSON to {out_file}")
        except Exception as e:
            print(f"✗ Failed on {image_path.name}: {e}")

    print("\nBatch OCR 完成。")


In [21]:
# In a Jupyter cell, you would then call main like this:
# Set your desired paths here:
my_input_directory = r"D:\testing_data_SScale_tif" # E.g., "/Users/YourName/Documents/tiff_images"
my_output_directory = r"D:\ocr_output"             # E.g., "/Users/YourName/Documents/ocr_output"

# Call the main function with your paths
main(input_dir_path=my_input_directory, output_dir_path=my_output_directory)

✓ Tesseract is installed (version 5.5.0.20241111)


Batch OCR:   0%|                                                                               | 0/130 [00:00<?, ?it/s]


Processing utaustin_18873.tif ...
Cropping image with 50.0% overlap...
Created 468 overlapping crops
Performing OCR on crops with confidence threshold: 0.0...



100%|████████████████████████████████████████████████████████████████████████████████| 468/468 [02:13<00:00,  3.52it/s]


Removing duplicate detections...


...

Removing duplicate detections...
Found 133 unique text elements
✔ Saved JSON to D:\ocr_output\utaustin_19561.json

Processing utaustin_19588.tif ...
Cropping image with 50.0% overlap...
Created 195 overlapping crops
Performing OCR on crops with confidence threshold: 0.0...



Batch OCR:  99%|██████████████████████████████████████████████████████████████████▍| 129/130 [2:53:50<01:23, 83.10s/it]

Removing duplicate detections...
Found 94 unique text elements
✔ Saved JSON to D:\ocr_output\utaustin_19588.json

Processing utaustin_19597.tif ...
Cropping image with 50.0% overlap...
Created 234 overlapping crops
Performing OCR on crops with confidence threshold: 0.0...



Batch OCR: 100%|███████████████████████████████████████████████████████████████████| 130/130 [2:56:08<00:00, 81.30s/it]

Removing duplicate detections...
Found 389 unique text elements
✔ Saved JSON to D:\ocr_output\utaustin_19597.json

Batch OCR 完成。
